<center>  <h1> Bitcoin prices and the shape of the globe </h1></center>

[Why Bitcoin price is increasing amid Russia-Ukraine war](https://www.financialexpress.com/digital-currency/why-bitcoin-price-is-increasing-amid-russia-ukraine-war/2447933/)

# **¿Which could be the bitcoin price next week?**


## Read bitcoin data

In [1]:
using CSV, DataFrames, Dates, PlotlyJS, LinearAlgebra

dataBitcoin_ori = CSV.read("Datasets/Bitcoin.csv",DataFrame);
dataBitcoin_ori.Price .= replace.(dataBitcoin_ori.Price, "," => "");
dataBitcoin_ori.PriceFloat = parse.(Float64, dataBitcoin_ori.Price);
dataBitcoin_ori.Date = Dates.Date.(dataBitcoin_ori.Date, "u d, yyyy")
dataBitcoin_ori[1:10,:]

WebIO._IJuliaInit()

10×8 DataFrame
 Row │ Date        Price     Open      High      Low       Vol.     Change %   ⋯
     │ Date        String15  String15  String15  String15  String7  String7    ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ 2022-03-07  38014.8   38,420.6  38,543.2  37,597.7  2.14B    -1.01%     ⋯
   2 │ 2022-03-06  38403.1   39,396.3  39,668.1  38,115.0  1.93B    -2.52%
   3 │ 2022-03-05  39395.8   39,142.8  39,600.2  38,626.1  1.50B    0.65%
   4 │ 2022-03-04  39142.7   42,463.0  42,848.7  38,594.9  3.21B    -7.82%
   5 │ 2022-03-03  42463.0   43,912.8  44,077.2  41,840.8  74.11K   -3.30%     ⋯
   6 │ 2022-03-02  43912.8   44,420.3  45,294.2  43,361.3  80.82K   -1.14%
   7 │ 2022-03-01  44420.3   43,187.2  44,900.5  42,876.6  90.67K   2.85%
   8 │ 2022-02-28  43188.2   37,707.2  43,977.8  37,458.9  108.07K  14.59%
   9 │ 2022-02-27  37689.1   39,116.6  39,838.5  37,062.3  66.14K   -3.65%     ⋯
  10 │ 2022-02-26  39115.5   39,221.6  40,094.5  38,639.1  41.55K   -0.24%
                                                                1 column omitted

In [2]:
y = 34e3:100:48e3 |> collect
t = DateTime[]
t1 = DateTime[]
t2 = DateTime[]
xlim = Dates.DateTime.(["01/01/2020", "03/28/2022"], "m/d/Y")

for i in y
    push!(t,Dates.DateTime("02/24/2022", "m/d/Y"))
    push!(t1,Dates.DateTime("03/07/2022", "m/d/Y"))
    push!(t2,Dates.DateTime("03/21/2022", "m/d/Y"))
end

pbit = plot([scatter(x=dataBitcoin_ori.Date, y= dataBitcoin_ori.PriceFloat, mode="markers+lines", name="Price",  legend=:topright),
        scatter(;x = t, y = y, name="War"), scatter(;x = t1, y = y, name="2W War"), scatter(;x = t2, y = y, name="1M War")],
             Layout(yaxis_range=(36e3,46e3),title="Bitcoin Price at 2022",  xaxis_title="Date (Month - Day)",  yaxis_title="Price (USD)"))
pbit

data: [
  "scatter with fields legend, mode, name, type, x, and y",
  "scatter with fields name, type, x, and y",
  "scatter with fields name, type, x, and y",
  "scatter with fields name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

Least squares formulation:

$$\tilde{x} = \mbox{arg min}_{x} \| Ax - b \|_2^2$$

In [3]:
N = size(dataBitcoin_ori.PriceFloat,1);  # total of samples
A = Array((1:N));                    #
b = Array(dataBitcoin_ori.PriceFloat);   #
A = [ones(N,1) A];
println("Matrix A: \n",size(A),A)
println(" ")
println("Matrix b: \n",size(b),b)

Matrix A: 
(29, 2)[1.0 1.0; 1.0 2.0; 1.0 3.0; 1.0 4.0; 1.0 5.0; 1.0 6.0; 1.0 7.0; 1.0 8.0; 1.0 9.0; 1.0 10.0; 1.0 11.0; 1.0 12.0; 1.0 13.0; 1.0 14.0; 1.0 15.0; 1.0 16.0; 1.0 17.0; 1.0 18.0; 1.0 19.0; 1.0 20.0; 1.0 21.0; 1.0 22.0; 1.0 23.0; 1.0 24.0; 1.0 25.0; 1.0 26.0; 1.0 27.0; 1.0 28.0; 1.0 29.0]
 
Matrix b: 
(29,)[38014.8, 38403.1, 39395.8, 39142.7, 42463.0, 43912.8, 44420.3, 43188.2, 37689.1, 39115.5, 39209.6, 38339.2, 37224.6, 38248.2, 37017.7, 38355.0, 40090.3, 40000.1, 40552.8, 43883.6, 44544.4, 42550.3, 42061.1, 42205.2, 42388.4, 43521.0, 44388.9, 44038.2, 43833.9]


In [4]:
size(A,1)

29

## Plot the **objective function**:

$$ f(x,y) = \sum_1^{N} (A\cdot X-b)\cdot(A\cdot X - b)^t $$

with $X = (x,y)^t$.

In [5]:
function f(x,y) 
    sum((A[:,1]*x+A[:,2]*y-b)*transpose((A[:,1]*x+A[:,2]*y-b)))
end

M = 100
x = LinRange(-5e4, 5e4, M)
y = LinRange(-5e4, 5e4, M)

F = Array{Float64}(undef,M,M)

for i in 1:1:M, j in 1:1:M
    F[i,j] = f(x[i],y[j])
end

PlotlyJS.plot([PlotlyJS.surface(x=x,y=y,z=F)])

data: [
  "surface with fields type, x, y, and z"
]

layout: "layout with fields margin and template"

Least squares solution:

$$\tilde{x} = \mbox{arg min}_{x} J(\mathbf x) = \mbox{arg min}_{x} \| Ax - b \|_2^2 \\
J(x) = \| Ax - b\|_2^2 = ( Ax - b )^T ( Ax - b ) = (A x)^T (A x) - (A x)^T b - b^T (A x) + b^T b\\
J(x) = x^T A^T Ax - 2 x^T A^T b + b^T b $$

Now **minimizing** $J(x)$ w.r.t $x$:

$$ \frac{\partial J(x)}{\partial  x} = - 2 A^T b + 2 A^T A x = 0 $$

We obtain the [normal equations](https://en.wikipedia.org/wiki/Linear_least_squares#Derivation_of_the_normal_equations):

$$A^T A x = A^T b$$

The solution:

$$x = (A^T A)^{-1} A^T  b = A^+ b$$

With $A^+ = (A^T A)^{-1} A^T$ the Moore-Penrose pseudoinverse of $A$.

# Arrange data to compute least squares

Structure data to compute least squares:

## Least solution Squares in Julia

https://www.matecdev.com/posts/julia-least-squares-qr.html

* Using the unique least squares approximate solution of overdetermined equations:

$$(A^T A)^{-1} A^T$$

In [6]:
transpose(A)*A

2×2 Matrix{Float64}:
  29.0   435.0
 435.0  8555.0

In [7]:
beta1 = inv(transpose(A)*A)*(transpose(A)*b)

2-element Vector{Float64}:
 38722.22783251229
   150.0073399014782

* Using the Moore-Penrose pseudoinverse:

In [8]:
xhat2 = pinv(A)*b

2-element Vector{Float64}:
 38722.227832512304
   150.0073399014782

* Solving the normal equations:

$$A^T A x = A^T b$$

In [9]:
x = transpose(A)*A \ transpose(A)*b

2-element Vector{Float64}:
 38722.22783251232
   150.00733990147745

* Using the QR solution:

In [10]:
xhat3 = A\b

2-element Vector{Float64}:
 38722.227832512304
   150.00733990147828

* There are cases where we want to obtain and store the matrices Q and R from the factorization:

In [11]:
qrA = qr(A);                    # QR decomposition
xhat4 = qrA\b

2-element Vector{Float64}:
 38722.22783251231
   150.00733990147774

In [12]:
pred = xhat4[2]*A[:,2] + xhat4[1]*A[:,1]

plot([scatter(x=dataBitcoin_ori.Date, y=dataBitcoin_ori.PriceFloat/1000, mode="markers+lines", name="Price"),
      scatter(x=dataBitcoin_ori.Date, y=pred[:,1]/1000, mode="markers+lines", name="Prediction")],
     Layout(title="Bitcoin Price at 2022",  xaxis_title="Time (day - month)",  yaxis_title="Price (k\$)"))

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [13]:
#LinSolver(A,1)

## Fitting an ellipse as Meyer (non-linear models)

Let's focus in an interesting curve-fitting problem, where we are given $n$ pairs of points 
$x_i,y_i$ and we want to find the ellipse which provides the best fit.

An idea can be start with the general conic that should satisfy this model:

$$a x^2 + bxy + c y^2 + dx + ey + f = 0$$

(Note that this is a second order equation, that will be quite important later in the course)

This model can be alternatively formulated as:

$$a x^2 + bxy + c y^2 + dx + ey = 1$$

Points in a particular ellipse should "satisfy" this equation (model). A particular ellipse (model) is parametrized by specific values of $a,b,c,d,e$. 

Therefore, given a set of observations $\{(x_i,y_i)_1^n\}$ the problem is find $a,b,c,d,e$ such that the following set of equations are satisfied:

$$a x_i^2 + b x_i y_i + c y_i^2 + dx_i + ey_i = 1, \qquad 1 \le i \le n$$

This problem can be formulated as a least squares problem by specifying a proper design matrix $A$, and solve the problem by using the previous formulation.

Let's generate noisy points around the ellipse.

In [14]:
θ = π/5; a = 2; b = 1.5; x_0 = 0; y_0 = 0;
fx(t) = a*cos(θ)*cos(t) - b*sin(θ)*sin(t) + x_0
fy(t) = a*sin(θ)*sin(t) + b*cos(θ)*cos(t) + y_0

N = 200;
ts = LinRange(0,2π,N);
x = fx.(ts) + randn(N)*0.1;
y = fy.(ts) + randn(N)*0.1;

plot([scatter(x=fx.(ts), y=fy.(ts), mode="line", name="Original Data"), 
      scatter(x=x, y=y, mode="markers", name="Noisy Data")],
     Layout(title="Non Linear Models - Data Creation",  xaxis_title="x",  yaxis_title="y"))

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

Now we can construct the design matrix.

In [15]:
A = [x.^2 y.^2 x.*y x y ];
dump(A)

Array{Float64}((200, 5)) [2.7732558552268864 1.0595900472404012 … 1.665309537361414 1.0293639041856875; 1.9259285664954444 1.9497532263004502 … 1.3877782843435202 1.3963356424228561; … ; 3.5023833751419 1.4074735687655104 … 1.8714655687834334 1.1863699122809506; 2.4673552636487455 1.4544484999053888 … 1.5707817364766963 1.2060051823708673]


We solve the least square problem by using the QR decomposition.

In [16]:
p = A\ones(N)

5-element Vector{Float64}:
  0.3166772171185263
  0.37968961733426926
 -0.2014744356261729
  0.008028064932060007
  0.010722861888682555

In [17]:
using Convex, SCS

b_t = ones(N)

# Create a (column vector) variable of size n x 1.
x_t = Variable(size(A,2))

# The problem is to minimize ||Ax - b||^2
# This can be done by: minimize(objective, constraints)
problem = minimize(square(norm(A * x_t - b_t)))

# Solve the problem by calling solve!
solve!(problem, SCS.Optimizer; silent_solver = true)

# Check the status of the problem
problem.status # :Optimal, :Infeasible, :Unbounded etc.

# Get the optimum value
p = x_t.value

5×1 Matrix{Float64}:
  0.31667721711836694
  0.37968961733410045
 -0.20147443562584644
  0.008028064932059174
  0.010722861888672695

We plot the solution:

In [18]:
X = LinRange(minimum(x),maximum(x),100)
Y = LinRange(minimum(y),maximum(y),100)
F = Array{Float64}(undef,100,100)

for i in 1:100, j in 1:100
    F[i,j] = p[1]*X[i]^2 + p[2]*Y[j]^2 + p[3]*X[i]*Y[j] + p[4]*X[i] + p[5]*Y[j]
end

plot([scatter(x=fx.(ts), y=fy.(ts), mode="line", name="Original Data", marker_color=:black),
      scatter(x=x, y=y, mode="markers", marker=attr(size=10, line_width=2, color=:yellow), name="Noisy Data"),
      contour(x=X, y=Y, z=F, linewidth=13, color=:green, name="Fitted Ellipse",  fill = false,  
        contours_coloring="lines",
        contours=attr(
            coloring ="heatmap",
            showlabels = true, # show labels on contours
            labelfont = attr(size = 12,color = "white",) # label font properties
        ),
        colorbar=attr(
            title="Level Contour", # title here
            titleside="right",
            titlefont=attr(size=14, family="Arial, sans-serif") )
     )], 
     Layout(title="Non Linear Models",  xaxis_title="x",  yaxis_title="y", 
        legend=attr(x=1, y=1.02, yanchor="bottom", xanchor="right", orientation="h")))

data: [
  "scatter with fields marker, mode, name, type, x, and y",
  "scatter with fields marker, mode, name, type, x, and y",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, y, and z"
]

layout: "layout with fields legend, margin, template, title, xaxis, and yaxis"

In [19]:
# Testing NonLinearSolver function
#=
f(i,j,p,X,Y) = p[1]*X[i]^2 + p[2]*Y[j]^2 + p[3]*X[i]*Y[j] + p[4]*X[i] + p[5]*Y[j]
Fp, Xp, Yp, pp = NonLinSolver([x.^2 y.^2 x.*y x y ];, 1, f, x, y, ones(size(Ag,1)));
Plot(x,y,Xp,Yp,Fp,"Test")
=#

# Homework 1

* Related with the nature of the data, which conditions should meet matrices $A$ and $b$ to be solvable from the least squares perspective.

* Use a least squares for non-linear models adjust the bitcoin price and perform a prediction using the model to determine the future daily price a week ahead, compare with the actual values.

* Use least squares to determine the relationship between the bitcoin price and prices of three comodities namely, oil, silved and gold, during the last year.

* Solve the [point set registration problem](https://en.wikipedia.org/wiki/Point-set_registration). Hint (check: S. Umeyama, Least-Squares Estimation of Transformation Parameters Between Two Point Patterns, IEEE Trans. Pattern Anal. Mach. Intell., vol. 13, no. 4, 1991). Construct a GUI to test.

# Solution

In [20]:
dataBitcoin = CSV.read("Datasets/Bitcoin1.csv", DataFrame);
dataSilver  = CSV.read("Datasets/Silver.csv",  DataFrame);
dataOil     = CSV.read("Datasets/Crude Oil WTI.csv",     DataFrame);
dataGold    = CSV.read("Datasets/Gold.csv",    DataFrame);

dataBitcoin.Date = Dates.Date.(dataBitcoin.Date, "m/d/yyyy");
dataSilver.Date  = Dates.Date.(dataSilver.Date, "m/d/yyyy");
dataOil.Date     = Dates.Date.(dataOil.Date, "m/d/yyyy");
dataGold.Date    = Dates.Date.(dataGold.Date, "m/d/yyyy");

In [21]:
y = 0:0.1:70 |> collect
t = DateTime[]
for i in y
    push!(t,Dates.DateTime("02/24/2022", "m/d/Y"))
end

plot([scatter(x=dataBitcoin.Date, y= dataBitcoin.Price/1000, mode="markers+lines", name="Price",  legend=:topright),
       scatter(;x = t, y = y, name="War Beginning") ],
             Layout(title="Bitcoin Price Whole History",  xaxis_title="Time (year)",  yaxis_title="Price (k\$)"))

data: [
  "scatter with fields legend, mode, name, type, x, and y",
  "scatter with fields name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

In [22]:
p1 = plot(scatter(x=dataGold.Date,    y=dataGold.Price,         mode="markers+lines", name="Gold"), 
           Layout( xaxis_range=xlim, title="Bitcoin",  xaxis_title="Time (month- day)",  yaxis_title="Price (USD)"));
p2 = plot(scatter(x=dataSilver.Date,  y=dataSilver.Price,       mode="markers+lines", name="Silver"), 
           Layout( xaxis_range=xlim, title="Silver",  xaxis_title="Time (month - day)",  yaxis_title="Price (USD)"));
p3 = plot(scatter(x=dataOil.Date,     y=dataOil.Price,          mode="markers+lines", name="Oil"), 
           Layout( xaxis_range=xlim, title="Oil",  xaxis_title="Time (month - day)",  yaxis_title="Price (USD)"));
p4 = plot(scatter(x=dataBitcoin.Date, y=dataBitcoin.Price, mode="markers+lines", name="Bitcoin"), 
           Layout( xaxis_range=xlim, title="Gold",  xaxis_title="Time (month - day)",  yaxis_title="Price (USD)"));

p = [p1 p2; p3 p4]
relayout!(p, title_text="Variables as a time function", xlim=xlim)
p

data: [
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis"
]

layout: "layout with fields annotations, margin, template, title, xaxis1, xaxis2, xaxis3, xaxis4, xlim, yaxis1, yaxis2, yaxis3, and yaxis4"

## Cleaning Data

In [23]:
data_range = reverse(Dates.DateTime("01/01/2022", "m/d/Y") : Day(1) : Dates.DateTime("04/01/2022", "m/d/Y") )
sizes = [size(dataGold.Date)[1] size(dataSilver.Date)[1] size(dataOil.Date)[1] size(dataBitcoin.Date)[1]]
min_size = minimum(sizes)

dataBitcoin_range = DataFrame(Date=Date[], Price=Float64[])
dataSilver_range  = DataFrame(Date=Date[], Price=Float64[])
dataGold_range    = DataFrame(Date=Date[], Price=Float64[])
dataOil_range     = DataFrame(Date=Date[], Price=Float64[])

for i in 1:1:size(data_range)[1]
    IndexOil     = findall((dataOil.Date .== data_range[i]))
    IndexGold    = findall((dataGold.Date .== data_range[i]))
    IndexSilver  = findall((dataSilver.Date .== data_range[i]))
    IndexBitcoin = findall((dataBitcoin.Date .== data_range[i]))
    
    if size(IndexOil)[1] != 0 && size(IndexGold)[1] != 0 && size(IndexSilver)[1] != 0 && size(IndexBitcoin)[1] != 0
        push!(dataOil_range,     (data_range[i], dataOil.Price[i]))
        push!(dataSilver_range,  (data_range[i], dataSilver.Price[i]))
        push!(dataGold_range,    (data_range[i], dataGold.Price[i]))
        push!(dataBitcoin_range, (data_range[i], dataBitcoin.Price[i]))
    end
end

In [24]:
y = 34e3:100:48e3 #|> collect
t = DateTime[]
t1 = DateTime[]
t2 = DateTime[]

xlim1 = Dates.DateTime.(["02/06/2022", "03/21/2022"], "m/d/Y")

for i in y
    push!(t,Dates.DateTime("02/24/2022", "m/d/Y"))
    push!(t1,Dates.DateTime("03/07/2022", "m/d/Y"))
    push!(t2,Dates.DateTime("03/21/2022", "m/d/Y"))
end

p1 = plot([scatter(x=dataBitcoin.Date, y=dataBitcoin.Price, mode="markers+lines", name="Price Downloaded"),
           scatter(x=dataBitcoin_ori.Date, y= dataBitcoin_ori.PriceFloat, mode="markers+lines", name="Price Professor"),
          scatter(;x = t, y = y, name="War"), scatter(;x = t1, y = y, name="2W - War"), scatter(;x = t2, y = y, name="1M - War")], 
           Layout(xaxis_range=xlim1, yaxis_range=(36e3,46e3), title="Bitcoin vs Time - Dataset Donwloaded",  xaxis_title="Date (Month - Day)",  yaxis_title="Price (USD)"))
p1

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields name, type, x, and y",
  "scatter with fields name, type, x, and y",
  "scatter with fields name, type, x, and y"
]

layout: "layout with fields margin, template, title, xaxis, and yaxis"

Even if both datasets have equal number of elements, Bitcoin.csv and Bitcoin1.csv, the Bitcoin1 file is choosed since has more historical data, this will help to plot the bitcoin - oil, silver, and gold relations

In [25]:
function LinSolver(A, flat)
    # 1: ls approximation 
    # 2: Penrose Pseudoinverse
    # 3: normal equations
    # 4: QR descomposition
    
    N = size(A,1)
    
    if flat == 1
        x = inv(transpose(A)*A)*(transpose(A)*b)
    elseif flat == 2
        x = pinv(A)*b
    elseif flat == 3
        x = transpose(A)*A \ transpose(A)*b      
    elseif flat == 4 
        xhat3 = A\b
        qrA = qr(A);                    # QR decomposition
        x = qrA\b
    end
    return x[2]*A[:,2] + x[1]*ones(N,1)
end

function NonLinSolver(A, flat, f, x, y, b)
    # 1: QR descomposition
    # 2: minimizing LS
    #b = ones(size(A,1))
    if flat == 1
        p = A\b
        #return p
    elseif flat == 2
        b_t = b # ones(size(A,1))
        x_t = Variable(size(A,2))
        problem = minimize(square(norm(A * x_t - b_t)))
        solve!(problem, SCS.Optimizer; silent_solver = true)
        problem.status # :Optimal, :Infeasible, :Unbounded etc.
        p = x_t.value
    end
    X = LinRange(minimum(x),maximum(x),100)
    Y = LinRange(minimum(y),maximum(y),100)
    F = Array{Float64}(undef,100,100)
    for i in 1:100, j in 1:100
        F[i,j] = f(i,j,p,X,Y) # = p[1]*X[i]^2 + p[2]*Y[j]^2 + p[3]*X[i]*Y[j] + p[4]*X[i] + p[5]*Y[j]
    end
    return (F, X, Y, p)
end

NonLinSolver (generic function with 1 method)

Let's formulate the problem using matrix notation and different fitting functions
* **Quadratic** $y = ax^2+bx +c $ that for $N$ points can be write as $a x_i+bx_i^2+c=y_i$
* **Exponential** $y = ae^{cx}+b$ that for $N$ points can be write as $a y_i + be^{cx}=1$


In [26]:
data_range_plot = Dates.DateTime("02/07/2022", "m/d/Y") : Day(1) : Dates.DateTime("03/21/2022", "m/d/Y") 
Np = size(data_range_plot,1);

N = size(dataBitcoin_ori.PriceFloat,1);  # total of samples
b = Array(dataBitcoin_ori.PriceFloat);   #

In [27]:
Aq = [Array((1:N)) Array((1:N)).^2 ones((N,1))];   #  a b c  (x, x^2, 1)
Aqp = [Array((1:Np)) Array((1:Np)).^2 ones((Np,1))];   #  a b c  (x, x^2, 1)

f(i,j,p,X,Y) = p[1]*X[i] + p[2]*X[i]^2 + p[3]  
Fq, Xq, Yq, pq = NonLinSolver(Aq, 1, f, Aq[:,1], Aq[:,2], b);

preq = pq[1]*Aqp[:,1] .+ pq[2]*Aqp[:,2] .+ pq[3]*Aqp[:,3];

* **Lineal** $y = mx+b$ that for $N$ points can be write as $a x_i + b=y_i$

In [28]:
Al = [Array((1:N))  ones((N,1))];      # x b
Alp = [Array((1:Np))  ones((Np,1))];   # x b 

f(i,j,p,X,Y) = p[1]*X[i] + p[2]
Fl, Xl, Yl, pl = NonLinSolver(Al, 1, f, Al[:,1], Al[:,2], b);

prel = pl[1]*Alp[:,1] .+ pl[2]*Alp[:,2];

* **Exponential** $y = Ae^{cx}+b$, $ln (y -b)= cx+lnA$  that for $N$ points can be write as $cX+lnA\mathbb{1} = ln (Y-b) $ or $C'X+A'\mathbb{1} = B' $

In [29]:
Ae = [Array((1:N))  ones((N,1))];   # x 1
Alp = [Array((1:Np))  ones((Np,1))];   # x 1

f(i,j,p,X,Y) = p[1]*X[i] + p[2]
Fe, Xe, Ye, pe = NonLinSolver(Ae, 1, f, Ae[:,1], Ae[:,2], log.(b));

pree =  exp.(pe[2]) * exp.(pe[1]*Alp[:,1])  #pe[1]*Alp[:,1] .+ pl[2]*;

In [30]:
dataBitcoin_range_plot = Dates.DateTime("02/07/2022", "m/d/Y") : Day(1) : Dates.DateTime("03/21/2022", "m/d/Y")

p1 = plot([scatter(x=dataBitcoin.Date, y=dataBitcoin.Price, mode="markers+lines", name="Real Price"),
           scatter(x=dataBitcoin_ori.Date, y=dataBitcoin_ori.PriceFloat, mode="markers+lines", name="Price Professor"),
           scatter(x=data_range_plot, y=preq, name="Quadratic Fitting", mode="markers+lines"),
           scatter(x=data_range_plot, y=pree, name="Exp Fitting", mode="markers+lines"),
           scatter(x=data_range_plot, y=prel, name="Lineal Fitting", mode="markers+lines")],
          Layout(xaxis_range=xlim1, yaxis_range=(36e3,50e3), title="Bitcoin vs Time",  yaxis_title="Price (USD)"))

p2 = plot([scatter(x=dataBitcoin.Date, y=dataBitcoin.Price, mode="markers+lines", name="Real Price"),
           scatter(x=data_range_plot, y=(preq), name="Quadratic Fitting", mode="markers+lines"),
           scatter(x=data_range_plot, y=pree, name="Exp Fitting", mode="markers+lines"),
           scatter(x=data_range_plot, y=prel, name="Lineal Fitting", mode="markers+lines")],
          Layout(xaxis_range=xlim1, yaxis_range=(36e3,50e3), title="Absolute Error",  xaxis_title="Date (Month - Day)",  yaxis_title="Error "))
[p1; p2]

data: [
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis"
]

layout: "layout with fields annotations, margin, template, xaxis1, xaxis2, yaxis1, and yaxis2"

## Bitcoin vs Oil, Gold, and Silver

In [31]:
p1 = plot(scatter(x=dataBitcoin_range.Price,    y=dataGold_range.Price,         mode="markers", name="Gold"), 
           Layout( title="Gold",  xaxis_title="Bitcoin (USD)",  yaxis_title="Price (USD)"));
p2 = plot(scatter(x=dataBitcoin_range.Price,  y=dataSilver_range.Price,       mode="markers", name="Silver"), 
           Layout( title="Silver",  xaxis_title="Bitcoin (USD)"));
p3 = plot(scatter(x=dataBitcoin_range.Price,     y=dataOil_range.Price,          mode="markers", name="Oil"), 
           Layout( title="Oil",  xaxis_title="Bitcoin (USD)"));
pl = plot([scatter(x=dataBitcoin_range.Price, y=dataGold_range.Price/maximum(dataGold_range.Price),         mode="markers", name="Gold"),
      scatter(x=dataBitcoin_range.Price,      y=dataSilver_range.Price/maximum(dataSilver_range.Price),       mode="markers", name="Silver"),
      scatter(x=dataBitcoin_range.Price,      y=dataOil_range.Price/maximum(dataOil_range.Price),          mode="markers", name="Oil")], 
           Layout( title="Normalazid Bitcoin vs Oil, Silver, and Gold",  xaxis_title="Bitcoin (USD)",  yaxis_title="Variable (normalized))"));

p = [p1 p2 p3; pl]

data: [
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields mode, name, type, x, xaxis, y, and yaxis"
]

layout: "layout with fields annotations, margin, template, xaxis1, xaxis2, xaxis3, xaxis4, yaxis1, yaxis2, yaxis3, and yaxis4"

In [32]:
function Plot(x,y,Xg,Yg,Fg,title)
    return plot([scatter(x=x, y=y, mode="markers", marker=attr(color=:black)),
                  contour(x=Xg, y=Yg, z=Fg, linewidth=13, color=:green, name="Fitted Ellipse",  fill = false,  
                        contours_coloring="lines",
                        contours=attr(  
                            coloring ="Electric",
                            showlabels = true, # show labels on contours
                            labelfont = attr(size = 12,color = "white",)  ),
                        colorbar=attr(
                            title="Level Contour", # title here
                            #title=attr(title_text="Level Contour"),
                            titleside="right",
                            titlefont=attr(size=14, family="Arial, sans-serif") ),
                        #contours_start=0.985, contours_end=1.005, contours_size=0.002
                ) ],
                  Layout(title=title,  xaxis_title="Bitcoin Price (USD)"));
end

Plot (generic function with 1 method)

* **Ellipse** $$a x_i^2 + b x_i y_i + c y_i^2 + dx_i + ey_i = 1, \qquad 1 \le i \le n$$

In [33]:
f(i,j,p,X,Y) = p[1]*X[i]^2 + p[2]*Y[j]^2 + p[3]*X[i]*Y[j] + p[4]*X[i] + p[5]*Y[j]

xg, yg =  dataBitcoin_range.Price, dataGold_range.Price
xs, ys =  dataBitcoin_range.Price, dataSilver_range.Price
xo, yo =  dataBitcoin_range.Price, dataOil_range.Price

Ag = [xg.^2 yg.^2 xg.*yg xg yg]
As = [xs.^2 ys.^2 xs.*ys xs ys]
Ao = [xo.^2 yo.^2 xo.*yo xo yo]

Fg, Xg, Yg, pg = NonLinSolver(Ag, 1, f, Ag[:,4], Ag[:,5], ones(size(Ag,1)));
Fs, Xs, Ys, ps = NonLinSolver(As, 1, f, As[:,4], As[:,5], ones(size(As,1)));
Fo, Xo, Yo, po = NonLinSolver(Ao, 1, f, Ao[:,4], Ao[:,5], ones(size(Ao,1)));

plotg = Plot(xg,yg,Xg,Yg,Fg,"Gold");
relayout!(plotg, yaxis_title="Price (USD)")
plots = Plot(xs,ys,Xs,Ys,Fs,"Silver");
ploto = Plot(xo,yo,Xo,Yo,Fo,"Oil");

plots = [plotg ploto plots]
relayout!(plots, title_text="Ellipse Fittings", showlegend=false)
          #legend=attr(x=1, y=1.02, yanchor="bottom", xanchor="right", orientation="h"))
plots

data: [
  "scatter with fields marker, mode, type, x, xaxis, y, and yaxis",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, xaxis, y, yaxis, and z",
  "scatter with fields marker, mode, type, x, xaxis, y, and yaxis",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, xaxis, y, yaxis, and z",
  "scatter with fields marker, mode, type, x, xaxis, y, and yaxis",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, xaxis, y, yaxis, and z"
]

layout: "layout with fields annotations, margin, showlegend, template, title, xaxis1, xaxis2, xaxis3, yaxis1, yaxis2, and yaxis3"

In [34]:
#Fo
#plot(scatter(x=xo, y=Fo[2,:]*maximum(yo), mode="markers"))

* **Circles** $$a x_i^2 + d = y_i^2, \qquad 1 \le i \le n$$
* **Circles** $$a x_i^2 + b y_i^2 +c =1, \qquad 1 \le i \le n$$

In [35]:
f(i,j,p,X,Y) = p[1]*X[i]^2 + p[2]*Y[j]^2# + p[3]

Ag = [xg.^2 yg.^2]# ones(size(xg,1))]
As = [xs.^2 yg.^2]# ones(size(xg,1))]
Ao = [xo.^2 yg.^2]# ones(size(xg,1))]

Fg, Xg, Yg, pg = NonLinSolver(Ag, 1, f, xg, yg, ones(size(xg,1)));
Fs, Xs, Ys, ps = NonLinSolver(As, 1, f, xs, ys, ones(size(xg,1)));
Fo, Xo, Yo, po = NonLinSolver(Ao, 1, f, xo, yo, ones(size(xg,1)));

plotg = Plot(xg,yg,Xg,Yg,Fg,"Gold");
relayout!(plotg, yaxis_title="Price (USD)")
plots = Plot(xs,ys,Xs,Ys,Fs,"Silver");
ploto = Plot(xo,yo,Xo,Yo,Fo,"Oil");

plots = [plotg ploto plots]
relayout!(plots, title_text="Ellipse Fittings", showlegend=false)
          #legend=attr(x=1, y=1.02, yanchor="bottom", xanchor="right", orientation="h"))
plots

data: [
  "scatter with fields marker, mode, type, x, xaxis, y, and yaxis",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, xaxis, y, yaxis, and z",
  "scatter with fields marker, mode, type, x, xaxis, y, and yaxis",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, xaxis, y, yaxis, and z",
  "scatter with fields marker, mode, type, x, xaxis, y, and yaxis",
  "contour with fields color, colorbar, contours, fill, linewidth, name, transpose, type, x, xaxis, y, yaxis, and z"
]

layout: "layout with fields annotations, margin, showlegend, template, title, xaxis1, xaxis2, xaxis3, yaxis1, yaxis2, and yaxis3"

In [36]:
xsb, ysb = dataBitcoin_range.Price, dataSilver_range.Price
Aqsb = [x x.^2 ones((size(xsb,1),1))];   #  a b c  (x, x^2, 1)

f(i,j,p,X,Y) = p[1]*X[i] + p[2]*X[i]^2 + p[3]  
Fsb, Xsb, Ysb, psb = NonLinSolver(Aqsb, 1, f, xsb, ysb, ysb);

#preq = pq[1]*Aqp[:,1] .+ pq[2]*Aqp[:,2] .+ pq[3]*Aqp[:,3];
psb1 = Plot(xsb,ysb,Xsb,Ysb,Fsb," ","Oil","Oil",0)
plots1 = [psb1 psb1]
relayout!(plots1, title_text="Quadratic Fittings", legend=attr(x=-0.2, y=1.1,))
plots1

LoadError: ArgumentError: number of rows of each array must match (got (200, 200, 67))

 ## Point Set Registration Problem

In [37]:
n = 3
x = LinRange(1,100,n)

X = [0 0;  1 0; 0 2]  #[x 0.03*x.-1]    # [x, y, z]  z=0
Y = [0 0; -1 0; 0 2] #[x rand(Float64, size(x))]
p1 = plot(scatter(x=X[:,1],y=X[:,2], mode="markers", name="Points X", marker=attr(size=5)), Layout(xaxis_range=[-1, 1]))
p2 = plot(scatter(x=Y[:,1],y=Y[:,2], mode="markers", name="Point Y", marker=attr(size=7)), Layout(xaxis_range=[-1, 1]))
[p1 p2]

data: [
  "scatter with fields marker, mode, name, type, x, xaxis, y, and yaxis",
  "scatter with fields marker, mode, name, type, x, xaxis, y, and yaxis"
]

layout: "layout with fields margin, template, xaxis1, xaxis2, yaxis1, and yaxis2"

In [38]:
dump(X)

Array{Int64}((3, 2)) [0 0; 1 0; 0 2]


Let's consider two point set $X$ and $Y$, oth with dimensions $(N,1)$,

$$
\mu_x = \frac{1}{n}\sum_{i=1}^n x_i \\
\mu_y = \frac{1}{n}\sum_{i=1}^n y_i \\
\sigma_x^2 = \frac{1}{n}\sum_{i=1}^n |x_i-\mu_x|^2 \\
\sigma_y^2 = \frac{1}{n}\sum_{i=1}^n |y_i-\mu_y|^2 \\
\Sigma_{xy} = \frac{1}{n}\sum_{i=1}^n (y_i-\mu_y)(x_i-\mu_x)^T
$$

In [230]:
function Sig(X,muX)
    xx = zeros(size(X))
    for i=1:n
        xx[i,:] = reshape(X[i,:], size(muX)) - muX
    end
    return xx
end

#X, Y = [0 1 0;  0 0 2] , [0 -1 0; 0 0 2] 
X, Y = [0 0;  1 0; 0 2], [0 0; -1 0; 0 2]
n, m = size(X) # samples, dimension

muX, muY = sum(X,dims=1)/n, sum(Y,dims=1)/n
sigmaX2, sigmaY2 = sum(norm.(eachrow(Sig(X,muX))).^2, dims=1)[1,1]/n, sum(norm.(eachrow(Sig(Y,muY))).^2, dims=1)[1,1]/n
#sum(abs.(X.-muX).^2,dims=1)/n, sum(abs.(Y.-muY).^2,dims=1)/n
Sigma = transpose(X.-muX)*(Y.-muY)/n

2×2 Matrix{Float64}:
 -0.222222  -0.222222
  0.222222   0.888889

In [228]:
using Statistics
mux, muy = mean(X, dims=1), mean(X, dims=1)
cov(X; corrected=false)
cov(X, Y; corrected=false)

2×2 Matrix{Float64}:
 -0.222222  -0.222222
  0.222222   0.888889

In [268]:
U, D, V = svd(Sigma)
D = diagm(D)
if rank(Sigma) >= m-1
    if det(U)*det(V) == 1 #det(Sigma) >= 0
        S = Matrix{Float64}(I, m, m)  # Identity matrix of Float64 type
    else
        S = Matrix{Float64}(I, m, m)  # Identity matrix of Float64 type
        S[m,m]=-1
    end


    R = U * S * V
    c = trace(D*S)/sigmaX2
    t = muY - transpose(c*R*transpose(muX))
    error2 = sigmaY2 - trace(D*S)^2/sigmaX2
end

0.5333333333333334

true

In [271]:
dump(R)
dump(c)
dump(t)
dump(error2)

Array{Float64}((2, 2)) [-1.0 -1.1102230246251565e-16; 5.551115123125783e-17 -0.9999999999999998]
Float64 0.7211102550927978
Array{Float64}((1, 2)) [-0.09296324830240069 1.1474068367285317]
Float64 0.5333333333333334


In [259]:
function Xf(c,R,X,t)
    xx = zeros(size(X))
    for i=1:n
        xx[i,:] = c*R*X[i,:] + transpose(t)
    end
    return xx
end

Xf (generic function with 1 method)

In [272]:
Xf(c,R,X,t)

3×2 Matrix{Float64}:
 -0.0929632   1.14741
 -0.814074    1.14741
 -0.0929632  -0.294814

In [273]:
a = Xf(c,R,Y,t)

3×2 Matrix{Float64}:
 -0.0929632   1.14741
  0.628147    1.14741
 -0.0929632  -0.294814

In [282]:
plot([scatter(x=a[:,1],y=a[:,2], mode="markers", name="Model"), 
      scatter(x=X[:,1],y=X[:,2], mode="markers", name="X"), 
      scatter(x=Y[:,1],y=Y[:,2], mode="markers", name="Y")])
#[pp p1 p2]

data: [
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y",
  "scatter with fields mode, name, type, x, and y"
]

layout: "layout with fields margin and template"